### Import libraries

In [1]:
!pip install torchmetrics

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 763.4/763.4 kB 3.8 MB/s eta 0:00:00


In [2]:
import numpy as np
from tqdm.autonotebook import tqdm
import time as tm
import datetime as dt
import math

# Network
import torch
import torchvision
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F

# Dataset
from torch.utils.data import Dataset, DataLoader
from sklearn.model_selection import train_test_split
from torch.utils.data import Subset
import pandas as pd
from pandas.core.indexes.datetimelike import RangeIndex

# Metrics
import torch
import torchmetrics

# Saving metrics
from google.colab import files

<ipython-input-2-a8063539652b>:2: TqdmExperimentalWarning: Using `tqdm.autonotebook.tqdm` in notebook mode. Use `tqdm.tqdm` instead to force console mode (e.g. in jupyter console)
  from tqdm.autonotebook import tqdm


In [3]:
torch.manual_seed(42)
np.random.seed(42)

### Preparing dataloader

In [4]:
tickers = pd.read_csv('final_relevant_wiki_tickers.csv')

In [5]:
# Tatyana

class CustomDataset():
  def get_slices_matrix(self, time_series_dataset, window_length):
    time_series_dataset = time_series_dataset.loc[time_series_dataset.company.isin(tickers.Ticker.tolist()), :]
    time_series_array = torch.tensor(np.empty(shape=(time_series_dataset.shape[0], time_series_dataset.shape[1] - 1)), dtype = torch.float32)

    for i in range(0, time_series_dataset.shape[0]):
      time_series_array[i] = torch.tensor(time_series_dataset.iloc[i, 1:time_series_dataset.shape[1]], dtype = torch.float32)

    time_series_slices_matrix = \
      torch.tensor(np.empty(shape = (time_series_dataset.shape[1] - window_length, time_series_dataset.shape[0], window_length)), dtype = torch.float32)

    for i in range(0, time_series_dataset.shape[1] - window_length):
      time_series_slices_matrix[i] = time_series_array[:, i : i + window_length]

    return time_series_slices_matrix


  def get_data(self, time_series_dataset, window_length):
    time_series_slices_matrix = self.get_slices_matrix(time_series_dataset, window_length)
    time_series_matrix = \
    torch.tensor(np.empty(shape = (time_series_dataset.shape[1] - window_length, time_series_dataset.shape[0], window_length)), dtype = torch.float32)

    for i in range(0, time_series_dataset.shape[1] - window_length):
      time_series_matrix[i] = self.time_series_labelling(time_series_slices_matrix[i], self.threshold)

    return time_series_slices_matrix, time_series_matrix

  def __init__(self, time_series_dataset, window_length, threshold=0.1):
    self.threshold = threshold
    matrix_prices, matrix_labels = self.get_data(time_series_dataset, window_length)
    y = torch.tensor(np.empty(shape = (time_series_dataset.shape[1] - window_length, time_series_dataset.shape[0], 1)), dtype = torch.float32)
    x = torch.tensor(np.empty(shape = (time_series_dataset.shape[1] - window_length, time_series_dataset.shape[0], window_length - 1)), dtype = torch.float32)

    for i in range(0, time_series_dataset.shape[1] - window_length):
      x[i] = matrix_prices[i, :, 0:(window_length - 1)]
      y[i] = matrix_labels[i, :, window_length - 1].view(-1, 1)

    self.x = x
    self.y = y
    print(self.x.shape)
    print(self.y.shape)

  def __getitem__(self, index):
    return self.x[index], self.y[index]

  def __len__(self):
      return len(self.x)

  def time_series_labelling(self, time_series, threshold):
    labelled_time_series = torch.tensor(np.empty(shape = (61, time_series.shape[1])), dtype = torch.int64)
    for i in range(0, 61):
      labelled_time_series[i, 0] = 1
      for j in range(1, time_series.shape[1]):
        if time_series[i, j] - time_series[i, j - 1] > 0:
          labelled_time_series[i, j] = 1
        if time_series[i, j] - time_series[i, j - 1] <= 0:
          labelled_time_series[i, j] = 0
    return labelled_time_series

In [6]:
time_series_dataset = pd.read_csv('time_series_NaN.csv', sep=',', header=0)

In [7]:
time_series_dataset = time_series_dataset.loc[time_series_dataset.company.isin(tickers.Ticker.tolist()), :]

In [8]:
data_scaling = time_series_dataset.copy()
data_scaling.iloc[:, 1:] = (data_scaling.iloc[:, 1:].T / data_scaling.max(axis = 1)).copy().T
data_scaling

<ipython-input-8-5261608ba408>:2: FutureWarning: Dropping of nuisance columns in DataFrame reductions (with 'numeric_only=None') is deprecated; in a future version this will raise TypeError.  Select only valid columns before calling the reduction.
  data_scaling.iloc[:, 1:] = (data_scaling.iloc[:, 1:].T / data_scaling.max(axis = 1)).copy().T


company  2017-01-03  2017-01-04  2017-01-05  2017-01-06  2017-01-09  \
1      AAPL    0.395539    0.395096    0.397105    0.401532    0.405210   
4      ADBE    0.312440    0.314432    0.319777    0.326993    0.327808   
7      ADSK    0.410940    0.418168    0.414985    0.427770    0.429334   
8      ADTN    0.924490    0.946939    0.920408    0.908163    0.902041   
10     AKAM    0.730171    0.738383    0.751567    0.754160    0.756430   
..      ...         ...         ...         ...         ...         ...   
323     VIA    0.633547    0.649573    0.620726    0.616453    0.616453   
327    VRSK    0.494106    0.497995    0.496172    0.500547    0.496597   
335     WDC    0.652231    0.662659    0.662753    0.661155    0.675059   
339    WYNN    0.434023    0.448017    0.453774    0.458687    0.460275   
342    ZEUS    0.887226    0.929197    0.918978    0.876277    0.896350   

     2017-01-10  2017-01-11  2017-01-12  2017-01-13  ...  2019-12-17  \
1      0.405619    0.407798    0.406096    0.405381  ...    0.954912   
4      0.326872    0.329076    0.327868    0.327687  ...    0.974789   
7      0.431438    0.436239    0.435052    0.438667  ...    0.979016   
8      0.912245    0.912245    0.900000    0.908163  ...    0.384898   
10     0.759455    0.757726    0.755673    0.756646  ...    0.910849   
..          ...         ...         ...         ...  ...         ...   
323    0.612179    0.637821    0.639957    0.633547  ...    0.407692   
327    0.499818    0.502795    0.500182    0.502066  ...    0.916332   
335    0.665477    0.671207    0.664631    0.666980  ...    0.537717   
339    0.470597    0.461168    0.456255    0.449258  ...    0.662498   
342    1.000000    0.997080    0.956934    0.895256  ...    0.651095   

     2019-12-18  2019-12-19  2019-12-20  2019-12-23  2019-12-24  2019-12-26  \
1      0.952631    0.953584    0.951609    0.967138    0.968057    0.987264   
4      0.979408    0.989221    0.989161    0.993207    0.995290    1.000000   
7      0.991207    0.991369    0.986298    0.986730    0.992070    0.993850   
8      0.390204    0.387347    0.385306    0.392653    0.396327    0.400000   
10     0.917441    0.913227    0.938621    0.928355    0.926410    0.933002   
..          ...         ...         ...         ...         ...         ...   
323    0.405556    0.407265    0.400000    0.394017    0.400427    0.395726   
327    0.904363    0.900413    0.909466    0.908677    0.906368    0.904302   
335    0.537623    0.552090    0.574072    0.589009    0.584594    0.589948   
339    0.688353    0.693961    0.685078    0.695896    0.691976    0.699419   
342    0.645985    0.651095    0.638686    0.653650    0.655110    0.658759   

     2019-12-27  2019-12-30  2019-12-31  
1      0.986889    0.992746    1.000000  
4      0.998762    0.991365    0.995803  
7      1.000000    0.988780    0.989643  
8      0.397551    0.401224    0.403673  
10     0.934731    0.928031    0.933434  
..          ...         ...         ...  
323    0.398291    0.391880    0.394444  
327    0.902783    0.896524    0.907401  
335    0.583654    0.586003    0.596242  
339    0.693812    0.691678    0.689147  
342    0.644526    0.644161    0.654015  

[61 rows x 755 columns]

In [9]:
# Tatyana

# time_series_dataset - without scaling
# data_scaling - with
dataset = CustomDataset(data_scaling, 21, 0.003)
print(dataset.__len__())
first_data = dataset[1]
features, labels = first_data
print(features.shape, labels.shape)
print(features, labels)

torch.Size([734, 61, 20])
torch.Size([734, 61, 1])
734
torch.Size([61, 20]) torch.Size([61, 1])
tensor([[0.3951, 0.3971, 0.4015,  ..., 0.4142, 0.4132, 0.4384],
        [0.3144, 0.3198, 0.3270,  ..., 0.3437, 0.3423, 0.3423],
        [0.4182, 0.4150, 0.4278,  ..., 0.4378, 0.4388, 0.4385],
        ...,
        [0.6627, 0.6628, 0.6612,  ..., 0.7442, 0.7490, 0.7436],
        [0.4480, 0.4538, 0.4587,  ..., 0.5089, 0.5033, 0.4856],
        [0.9292, 0.9190, 0.8763,  ..., 0.8358, 0.8212, 0.7839]]) tensor([[0.],
        [0.],
        [1.],
        [0.],
        [1.],
        [1.],
        [0.],
        [1.],
        [1.],
        [0.],
        [0.],
        [0.],
        [0.],
        [1.],
        [1.],
        [1.],
        [1.],
        [1.],
        [1.],
        [0.],
        [1.],
        [0.],
        [1.],
        [1.],
        [1.],
        [1.],
        [0.],
        [0.],
        [0.],
        [0.],
        [1.],
        [1.],
        [1.],
        [1.],
        [0.],
        [0.],
  

In [10]:
train_border = math.floor(0.7 * dataset.__len__())
train_dataset = Subset(dataset, list(range(train_border)))
val_border = train_border + math.floor(0.1 * dataset.__len__())
val_dataset = Subset(dataset, list(range(train_border, val_border)))
test_dataset = Subset(dataset, list(range(val_border, dataset.__len__())))

In [11]:
train_dataloader = DataLoader(train_dataset, batch_size=64, shuffle=False)
test_dataloader = DataLoader(test_dataset, batch_size=64, shuffle=False)
val_dataloader = DataLoader(val_dataset, batch_size=64, shuffle=False)

### Sequential

In [12]:
# Ksenia

def MovingAvg(x, kernel_size, stride = 1):
    if kernel_size % 2 == 0:
        padding_size_left = kernel_size // 2 - 1
        padding_size_right = kernel_size // 2
    else:
        padding_size_left = (kernel_size - 1) // 2
        padding_size_right = (kernel_size - 1) // 2

    trend = torch.zeros((x.shape[0], x.shape[1], x.shape[2]), dtype=torch.float32)
    front = x[:, :, 0:1].repeat(1, 1, padding_size_left) # (batch_size, 61, 7)
    end = x[:, :, -1:].repeat(1, 1, padding_size_right) # (batch_size, 61, 7)

    x = torch.cat([front, x, end], dim=2)

    i = 0
    while i < x.shape[2] - kernel_size + 1:
        window_average = torch.sum(x[:, :, i:i+kernel_size], dim=2) / kernel_size
        trend[:, :, i] = window_average
        i += stride

    return trend

def SeriesDecomp(x, kernel_size): # (batch_size, 61, 15)
    moving_mean = MovingAvg(x, kernel_size, stride=1)
    res = x - moving_mean
    return res, moving_mean

In [13]:
# Ksenia

class SequentialModel(nn.Module):

  def __init__(self, time_series_length, hidden_size):
    super(SequentialModel, self).__init__()

    self.rnn1_season = nn.RNN(input_size = time_series_length, hidden_size=hidden_size, num_layers = 5, dropout = 0.2)
    self.rnn1_trend = nn.RNN(input_size = time_series_length, hidden_size=hidden_size, num_layers = 5, dropout = 0.2)
    self.batch_norm_season = nn.BatchNorm1d(61)
    self.batch_norm_trend = nn.BatchNorm1d(61)

    self.fc1_season = nn.Linear(time_series_length, hidden_size)
    self.fc1_trend = nn.Linear(time_series_length, hidden_size)

  def forward(self, x): # (batch_size, 61, 15)

    season, trend = SeriesDecomp(x, 7)

    season, _ = self.rnn1_season(season)
    season = nn.Tanh()(season)
    season = self.batch_norm_season(season)

    trend, _ = self.rnn1_trend(trend)
    trend = nn.Tanh()(trend)
    trend = self.batch_norm_trend(trend)

    x = torch.cat([season, trend], dim=2)
    # x = season + trend

    return(x)

### Relational

In [14]:
# Anastasiya

# First design: Naive way
class NaiveRelationalModel(torch.nn.Module):

  def __init__(self, connection_matrix, hidden_size):
    super(NaiveRelationalModel, self).__init__()

    self.hidden_size = hidden_size
    self.connection_matrix = torch.Tensor(connection_matrix)

  def forward(self, embedding):

    relational = torch.zeros((embedding.shape[0], embedding.shape[1], embedding.shape[2]))

    for i in range(embedding.shape[1]): # (1)

      a_i = self.connection_matrix[i]

      weighted = torch.multiply(a_i, embedding.permute(0, 2, 1)).permute(0, 2, 1) # (batch_size, comp_count, hidden_size)
      result = weighted.sum(dim=1) # (batch_size, 1, hidden_size)

      relational[:, i] = result / (a_i > 0).sum()

    return relational

In [15]:
# Anastasiya

# Second design: Weighted way
class RelationalModel(torch.nn.Module):

  def __init__(self, connection_matrix, hidden_size, modeling_type=True):
    super(RelationalModel, self).__init__()

    self.modeling_type = modeling_type
    self.hidden_size = hidden_size
    self.connection_matrix = torch.Tensor(connection_matrix)
    self.layers = []

    for i in range(self.connection_matrix.shape[0]):

      if self.modeling_type: # Explicit
      # По одному линейному слою для каждой компании
        self.layers.append(nn.Linear(61, 61))

      else: # Implicit
      # По одному линейному слою для каждой компании (общий для всех конкатенаций i-той компании)
        self.layers.append(nn.Linear(1 + 2 * hidden_size, hidden_size))


  def forward(self, embedding):

    # Создаем пустую матрицу, в которой потом будут пересчитанные эмбеддинги
    relational = torch.zeros((embedding.shape[0], embedding.shape[1], embedding.shape[2]))

    # Проходимся по всем компаниям
    for i in range(embedding.shape[1]): # в скобках размерности матриц

      # Получаем вектор связи для текущей компании
      a_i = self.connection_matrix[i] # (comp_count)

      if self.modeling_type: # Explicit
        #Применяем линейный слой к вектору связи = получаем скрытые веса, с которыми эмбеддинги других компаний войдут в новый для текущей компании
        weight = self.layers[i](a_i) # (comp_count)
        weight = nn.Softmax(dim=0)(weight) # (comp_count)

        # Если посмотреть на similarity_part и relation_part, то в сумме текущий эмбеддинг умножается на квадрат вектора эмбеддинга другой компании

        # Получаем квадраты эмбеддингов

        # Умножаем попарно, не матричное умножение
        similarity = torch.multiply(embedding, embedding) # (batch_size, comp_count, hidden_size)

        # Умножаем все квадраты на текущий эмбеддинг

        # permute меняет размерности местами, это нужно для torch.multiply - он требует, чтобы последние размерности были равными

        similarity = torch.multiply(embedding[:, i], similarity.permute(1, 0, 2)).permute(1, 0, 2) # (batch_size, comp_count, hidden_size)

        # Умножаем попарно полученные веса на квадрат * текущий эмбеддинг
        weighted = torch.multiply(weight, similarity.permute(0, 2, 1)).permute(0, 2, 1) # (batch_size, comp_count, hidden_size)

        # Зануляем эмбеддинги несвязанных с текущей компаний = условие {j | a_i_j > 0}
        weighted = torch.multiply(a_i, weighted.permute(0, 2, 1)).permute(0, 2, 1) # (batch_size, comp_count, hidden_size)

        # Суммируем все эмбеддинги компаний, связанных с текущей
        result = weighted.sum(dim=1) # (batch_size, 1, hidden_size)

      else: #Implicit

        # Сначала получаем конкатенации вектор имеет вид [e_i_1, ... , e_i_7, e_j_1, ... , e_j_7, a_i_j]
        emb = torch.zeros((embedding.shape[1], embedding.shape[0], 2 * self.hidden_size + 1)) # (comp_count, batch_size, hidden_size)
        for j in range(embedding.shape[1]):
          a_i_j = np.repeat(a_i[j], embedding.shape[0]).reshape(embedding.shape[0], 1)

          emb[j] = torch.cat([embedding[:, i], embedding[:, j], a_i_j], 1) # (batch_size, 2 * hidden_size)

        # Прогоняем через линейный слой = Получаем матрицу весов = отдельный вес для каждого батча, для каждой ячейки эмбеддингов
        # Для каждой компании своя такая матрица
        weight = self.layers[i](emb) # (comp_count, batch_size, hidden_size)
        weight = nn.Softmax(dim=2)(weight).permute(1, 0, 2) # (batch_size, comp_count, hidden_size)

        # Умножаем на эмбеддинги
        weighted = torch.multiply(weight, embedding) # (batch_size, comp_count, hidden_size)
        # Зануляем эмбеддинги несвязанных с текущей компаний = условие {j | a_i_j > 0}
        weighted = torch.multiply(a_i, weighted.permute(0, 2, 1)).permute(0, 2, 1) # (batch_size, comp_count, hidden_size)

        # Суммируем все эмбеддинги компаний, связанных с текущей
        result = weighted.sum(dim=1) # (batch_size, 1, hidden_size)

      # Делим на d_j = усреднение
      relational[:, i] = result / (a_i > 0).sum()

    return relational

### Prediction

In [16]:
# Tatyana
class PredictionModel(torch.nn.Module):

  def __init__(self, hidden_size):
    super(PredictionModel, self).__init__()
    self.first_linear = nn.Linear(hidden_size, 50)
    self.second_linear = nn.Linear(50, 1)
    self.dropout = nn.Dropout(p=0.1)

  def forward(self, x):
    first_output = self.first_linear(x)
    first_output = nn.Tanh()(first_output)
    x = self.second_linear(self.dropout(first_output))
    return x

### Common

In [17]:
# Anastasiya

class CommonModel(torch.nn.Module):

  def __init__(self, time_series_length, hidden_size, connection_matrix, is_baseline=False, is_naive=False, relation_type=True):
    super(CommonModel, self).__init__()
    self.sequential_model = SequentialModel(time_series_length, hidden_size)
    self.is_baseline = is_baseline

    if self.is_baseline:
      self.prediction_model = PredictionModel(2*hidden_size)
    else:
      if is_naive:
        self.relational_model = NaiveRelationalModel(connection_matrix, 2*hidden_size)
      else:
        self.relational_model = RelationalModel(connection_matrix, 2*hidden_size, modeling_type=relation_type)

      self.prediction_model = PredictionModel(2*hidden_size)

  def forward(self, ts_batch):
    embedding = self.sequential_model(ts_batch)

    # Если baseline, то не нужно пропускать эмбеддинги через слой пересчета
    if self.is_baseline:
      answer = self.prediction_model(embedding)
    else:
      relational = self.relational_model(embedding)
      answer = self.prediction_model(relational)

    return answer

## Classification

### Help methods

In [18]:
# Tatyana

accuracy_ = torchmetrics.classification.Accuracy(task='binary')
f1_ = torchmetrics.classification.F1Score(task='binary')
pres_ = torchmetrics.classification.Precision(task='binary')
rec_ = torchmetrics.classification.Recall(task='binary')
roc_ = torchmetrics.classification.BinaryAUROC()

In [19]:
# Tatyana

def get_metrics(y_pred, labels_batch):
  acc = accuracy_(y_pred, labels_batch) * 100
  f1 = f1_(y_pred, labels_batch)
  prec = pres_(y_pred, labels_batch)
  roc = roc_(y_pred, labels_batch)
  recall = rec_(y_pred, labels_batch)

  return acc, recall, prec, f1, roc

In [20]:
# Ksenia

def validate(model, val_dataloader):
  metrics_val = []

  with torch.no_grad():
    for val_ts_batch, val_labels_batch in val_dataloader:
        val_ts_batch = val_ts_batch.to(device)

        val_answer = model(val_ts_batch)
        val_pred = torch.sigmoid(val_answer)
        loss = criterion(val_pred, val_labels_batch)

        val_pred = torch.where(val_pred > 0.5, 1, 0)
        accuracy, recall, precision, f1, roc_auc = get_metrics(val_pred, val_labels_batch)
        metrics_val.append([loss, accuracy, recall, precision, f1, roc_auc])

  mean = torch.Tensor(metrics_val).mean(axis=0)
  val_loss, val_accuracy, val_recall, val_precision, val_f1, val_roc = mean
  return val_loss, val_accuracy, val_recall, val_precision, val_f1, val_roc

In [21]:
# Ksenia

def test(model, test_dataloader):
  metrics_val = []
  model.eval()

  with torch.inference_mode():
    for test_ts_batch, test_labels_batch in test_dataloader:
        test_ts_batch = test_ts_batch.to(device)

        test_answer = model(test_ts_batch)
        test_pred = torch.sigmoid(test_answer)
        loss = criterion(test_pred, test_labels_batch)

        test_pred = torch.where(test_pred > 0.5, 1, 0)
        accuracy, recall, precision, f1, roc_auc = get_metrics(test_pred, test_labels_batch)
        metrics_val.append([loss, accuracy, recall, precision, f1, roc_auc])

  mean = torch.Tensor(metrics_val).mean(axis=0)
  test_loss, test_accuracy, test_recall, test_precision, test_f1, test_roc = mean
  return test_loss, test_accuracy, test_recall, test_precision, test_f1, test_roc

In [22]:
# Tatyana

def train(train_dataloader, val_dataloader, file, model, optimizer):
  model.train()

  last_val_loss = 0
  difference = []
  flag = True
  count = 0
  epoch = 0

  for epoch in range(30):
    model.train()
    epoch += 1
    metrics_per_epoch = []

    for ts_batch, labels_batch in train_dataloader: # ts_batch (batch_size, 61, input_chunk_length)

      optimizer.zero_grad()

      ts_batch = ts_batch.to(device)
      labels_batch = labels_batch.to(device)

      answer = model(ts_batch)
      y_pred = torch.sigmoid(answer)
      loss = criterion(y_pred, labels_batch)
      y_pred = torch.where(y_pred > 0.5, 1, 0)

      print('Predicted: ')
      print('uniqs: ',y_pred.unique(return_counts=True)[1])
      print('Ground truth: ')
      print('uniqs: ',labels_batch.unique(return_counts=True)[1])
      print()

      acc, recall, prec, f1, roc = get_metrics(y_pred, labels_batch)
      metrics_per_epoch.append([loss, acc, recall, prec, f1, roc])

      loss.backward()
      optimizer.step()

    val_loss, val_accuracy, val_recall, val_precision, val_f1, val_roc_auc = validate(model, val_dataloader)
    mean = torch.Tensor(metrics_per_epoch).mean(axis=0)
    train_loss, train_accuracy, train_recall, train_precision, train_f1, train_roc_auc = mean

    print(f"Epoch: {epoch} | Mean Train Loss: {train_loss:.5f} | Mean Train Acc: {train_accuracy:.2f}% | Val Loss: {val_loss:.5f} | Val accuracy: {val_accuracy:.2f}%")
    print(f"Epoch: {epoch} | Mean Train F1: {train_f1:.5f} | Mean Train Precision: {train_precision:.5f} | Val F1: {val_f1:.5f} | Val precision: {val_precision:.5f}")
    print(f"Epoch: {epoch} | Mean Train ROC-AUC: {train_roc_auc:.5f} | Mean Train Recall: {train_recall:.5f} | Val ROC-AUC: {val_roc_auc:.5f} | Val Recall: {val_recall:.5f}")

    file.write(f"Epoch: {epoch} | Mean Train Loss: {train_loss:.5f} | Mean Train Acc: {train_accuracy:.2f}% | Val Loss: {val_loss:.5f} | Val accuracy: {val_accuracy:.2f}%\n")
    file.write(f"Epoch: {epoch} | Mean Train F1: {train_f1:.5f} | Mean Train Precision: {train_precision:.5f} | Val F1: {val_f1:.5f} | Val precision: {val_precision:.5f}\n")
    file.write(f"Epoch: {epoch} | Mean Train ROC-AUC: {train_roc_auc:.5f} | Mean Train Recall: {train_recall:.5f} | Val ROC-AUC: {val_roc_auc:.5f} | Val Recall: {val_recall:.5f}\n")

In [23]:
device = torch.device('cuda' if torch.cuda.is_available() else 'cpu')
criterion = nn.BCELoss()

### Saving metrics

In [24]:
base_dict = {'loss': 0, 'acc': 0, 'recall': 0, 'precision': 0, 'f1': 0, 'roc-auc': 0, 'model_name': 'None'}
metrics = pd.DataFrame(base_dict, index = RangeIndex(1))

### Eval model

In [25]:
# Anastasiya

random_state = [99, 40, 77, 25, 31]

def eval_model(model_name, is_baseline, is_naive=False, connection_matrix=None, relation_type=True):
  metrics_per_type = []

  for i in range(5):

    torch.manual_seed(random_state[i])
    np.random.seed(random_state[i])

    model = CommonModel(20, 100, connection_matrix, is_baseline=is_baseline, is_naive=is_naive, relation_type=relation_type)
    model.to(device)
    optimizer = optim.Adam(model.parameters(), lr=0.01)

    file = open(f'{model_name}_try{i}.txt', "w")
    train(train_dataloader, val_dataloader, file, model, optimizer)
    file.close()
    files.download(f'{model_name}_try{i}.txt')

    test_loss, test_acc, test_rec, test_prec, test_f1, test_roc = test(model, test_dataloader)
    print(f'Test Loss: {test_loss:.2f}, Test accuracy: {test_acc:.2f}%, Test F1: {test_f1:.5f}, Test precision: {test_prec:.5f}, Test ROC-AUC: {test_roc:.5f}, Test recall: {test_rec:.5f}')
    metrics_per_type.append([test_loss, test_acc, test_rec, test_prec, test_f1, test_roc])

  mean = np.array(metrics_per_type).mean(axis=0)
  metrics.loc[len(metrics.index) - 1] = np.append(mean, f'{model_name}')

  metrics.to_csv(f'{model_name}.csv')

  files.download(f'{model_name}.csv')

### Baseline Model

In [ ]:
# Baseline

eval_model('Baseline', True)

Predicted: 
uniqs:  tensor([2130, 1774])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3782,  122])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([1031, 2873])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([1520, 2384])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([2671, 1233])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.98502 | Mean Train Acc: 48.92% | Val Loss: 0.70519 | Val accuracy: 48.46%
Epoch: 1 | Mean Train F1: 0.38237 | Mean Train Precision: 0.37268 | Val F1: 0.41563 | Val precision: 0.43350
Epoch: 1 | Mean Train ROC-AUC: 0.49610 | Me

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.71, Test accuracy: 51.05%, Test F1: 0.59996, Test precision: 0.53756, Test ROC-AUC: 0.49551, Test recall: 0.67986
Predicted: 
uniqs:  tensor([3590,  314])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([  97, 3807])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([1812, 2092])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([1999, 1905])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([  23, 3881])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([ 938, 2966])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.86172 | Mean Train Acc: 49.11% | Val Loss: 0.69524 | Val accuracy: 49.32%
Epoch: 1 | Mean Tra

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.70, Test accuracy: 52.32%, Test F1: 0.59262, Test precision: 0.55174, Test ROC-AUC: 0.51272, Test recall: 0.64035


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

# Experiment

## Anastasiya: Endogenous linkages

### DTW

In [ ]:
matrix_dtw = np.load('DTW_Matrix_Scaling.npy')

In [ ]:
eval_model('DTW_Naive', is_baseline=False, is_naive=True, connection_matrix=matrix_dtw)

Predicted: 
uniqs:  tensor([2185, 1719])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3598,  306])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([  96, 3808])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([2622, 1282])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3304,  600])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([14, 47])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.88761 | Mean Train Acc: 50.09% | Val Loss: 0.68969 | Val accuracy: 54.06%
Epoch: 1 | Mean Train F1: 0.43459 | Mean Train Precision: 0.45624 | Val F1: 0.22556 | Val precision: 0.46785
Epoch: 1 | Mean Train ROC-AUC: 0.49372 

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 54.17%, Test F1: 0.70269, Test precision: 0.54172, Test ROC-AUC: 0.50000, Test recall: 1.00000
Predicted: 
uniqs:  tensor([3678,  226])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([ 861, 3043])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3681,  223])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([ 678, 3226])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([  54, 3850])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([1096, 2808])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.82732 | Mean Train Acc: 50.77% | Val Loss: 0.70181 | Val accuracy: 45.60%
Epoch: 1 | Mean Tra

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 54.17%, Test F1: 0.70269, Test precision: 0.54172, Test ROC-AUC: 0.50000, Test recall: 1.00000


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
eval_model('DTW_Explicit', is_baseline=False, is_naive=False, connection_matrix=matrix_dtw, relation_type=True)

Predicted: 
uniqs:  tensor([3144,  760])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([ 188, 3716])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([28, 33])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.70038 | Mean Train Acc: 52.07% | Val Loss: 0.69281 | Val accuracy: 49.55%
Epoch: 1 | Mean Train F1: 0.55887 | Mean Train Precision: 0.47987 | Val F1: 0.46671 | Val precision: 0.44076
Epoch: 1 | Mean Train ROC-AUC: 0.51067 | Mean Train Recal

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.70, Test accuracy: 49.18%, Test F1: 0.38140, Test precision: 0.55978, Test ROC-AUC: 0.51022, Test recall: 0.28926
Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([  10, 3894])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69975 | Mean Train Acc: 51.03% | Val Loss: 0.69454 | Val accuracy: 44.38%
Epoch: 1 | Mean Train F1: 0.46185 | Mean Train Pr

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.73, Test accuracy: 46.66%, Test F1: 0.22918, Test precision: 0.52841, Test ROC-AUC: 0.49570, Test recall: 0.14632


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
#eval_model('DTW_Implicit', is_baseline=False, is_naive=False, connection_matrix=matrix_dtw, relation_type=False)

### VRAE

In [33]:
matrix_vrae = np.load('matrix_vrae.npy')

In [34]:
eval_model('VRAE_Naive', is_baseline=False, is_naive=True, connection_matrix=matrix_vrae)

Predicted: 
uniqs:  tensor([2281, 1623])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([2780, 1124])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([1263, 2641])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([1925, 1979])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([1836, 2068])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.95852 | Mean Train Acc: 49.46% | Val Loss: 0.74778 | Val accuracy: 45.04%
Epoch: 1 | Mean Train F1: 0.42654 | Mean Train Precision: 0.40555 | Val F1: 0.53682 | Val precision: 0.43778
Epoch: 1 | Mean Train ROC-AUC: 0.49953 | Me

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 52.88%, Test F1: 0.63555, Test precision: 0.54694, Test ROC-AUC: 0.50825, Test recall: 0.75927
Predicted: 
uniqs:  tensor([3827,   77])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([ 122, 3782])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([ 125, 3779])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3262,  642])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3365,  539])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3317,  587])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.85750 | Mean Train Acc: 49.08% | Val Loss: 0.69248 | Val accuracy: 50.81%
Epoch: 1 | Mean Tra

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 51.56%, Test F1: 0.54904, Test precision: 0.55360, Test ROC-AUC: 0.51287, Test recall: 0.54458


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [35]:
eval_model('VRAE_Explicit', is_baseline=False, is_naive=False, connection_matrix=matrix_vrae, relation_type=True)

Predicted: 
uniqs:  tensor([3649,  255])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([1610, 2294])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([ 8, 53])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69272 | Mean Train Acc: 52.84% | Val Loss: 0.69699 | Val accuracy: 44.84%
Epoch: 1 | Mean Train F1: 0.61569 | Mean Train Precision: 0.53207 | Val F1: 0.60654 | Val precision: 0.44309
Epoch: 1 | Mean Train ROC-AUC: 0.51020 | Mean Train Recal

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.71, Test accuracy: 47.78%, Test F1: 0.29445, Test precision: 0.55013, Test ROC-AUC: 0.50286, Test recall: 0.20102
Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([  57, 3847])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([2466, 1438])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([ 229, 3675])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69469 | Mean Train Acc: 49.84% | Val Loss: 0.69576 | Val accuracy: 40.96%
Epoch: 1 | Mean Train F1: 0.50031 | M

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.70, Test accuracy: 52.62%, Test F1: 0.61418, Test precision: 0.54972, Test ROC-AUC: 0.51103, Test recall: 0.69625


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [36]:
#eval_model('VRAE_Implicit', is_baseline=False, is_naive=False, connection_matrix=matrix_vrae, relation_type=False)

### SOM

In [72]:
matrix_som = np.load('matrix_som.npy')

In [73]:
eval_model('SOM_Naive', is_baseline=False, is_naive=True, connection_matrix=matrix_som)

Predicted: 
uniqs:  tensor([2267, 1637])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3354,  550])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([1610, 2294])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([1983, 1921])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([1715, 2189])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.97595 | Mean Train Acc: 48.68% | Val Loss: 0.71429 | Val accuracy: 49.57%
Epoch: 1 | Mean Train F1: 0.40004 | Mean Train Precision: 0.39582 | Val F1: 0.51413 | Val precision: 0.45296
Epoch: 1 | Mean Train ROC-AUC: 0.49312 | Me

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.70, Test accuracy: 51.75%, Test F1: 0.64101, Test precision: 0.53693, Test ROC-AUC: 0.49234, Test recall: 0.79552
Predicted: 
uniqs:  tensor([3834,   70])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([ 122, 3782])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([  61, 3843])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([2438, 1466])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3799,  105])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3868,   36])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.86256 | Mean Train Acc: 49.04% | Val Loss: 0.68848 | Val accuracy: 55.39%
Epoch: 1 | Mean Tra

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 51.10%, Test F1: 0.56924, Test precision: 0.54439, Test ROC-AUC: 0.50323, Test recall: 0.59655


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [74]:
eval_model('SOM_Explicit', is_baseline=False, is_naive=False, connection_matrix=matrix_som, relation_type=True)

Predicted: 
uniqs:  tensor([3644,  260])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3820,   84])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([   1, 3903])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69263 | Mean Train Acc: 51.73% | Val Loss: 0.69655 | Val accuracy: 44.32%
Epoch: 1 | Mean Train F1: 0.55655 | Mean Train Precision: 0.53888 | Val F1: 0.61000 | Val precision: 0.44316
Epoch: 1 | Mean Train ROC-AUC: 0.50001 | Mean Train Rec

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.70, Test accuracy: 52.95%, Test F1: 0.67230, Test precision: 0.54011, Test ROC-AUC: 0.49708, Test recall: 0.89117
Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([  58, 3846])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([1340, 2564])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([ 649, 3255])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([31, 30])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69372 | Mean Train Acc: 51.79% | Val Loss: 0.69833 | Val accuracy: 44.13%
Epoch: 1 | Mean Train F1: 0.58220

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.71, Test accuracy: 52.20%, Test F1: 0.57720, Test precision: 0.55440, Test ROC-AUC: 0.51498, Test recall: 0.60239


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [75]:
#eval_model('SOM_Implicit', is_baseline=False, is_naive=False, connection_matrix=matrix_som, relation_type=False)

### K-Means

In [76]:
matrix_kmeans = np.load('matrix_kmeans.npy')

In [77]:
eval_model('KMeans_Naive', is_baseline=False, is_naive=True, connection_matrix=matrix_kmeans)

Predicted: 
uniqs:  tensor([2295, 1609])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([ 312, 3592])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3781,  123])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([1340, 2564])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([2859, 1045])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([2885, 1019])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.94324 | Mean Train Acc: 50.27% | Val Loss: 0.69905 | Val accuracy: 54.43%
Epoch: 1 | Mean Train F1: 0.42556 | Mean Train Precision: 0.43282 | Val F1: 0.26833 | Val precision: 0.51231
Epoch: 1 | Mean Train ROC-AUC: 0.4944

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.70, Test accuracy: 50.66%, Test F1: 0.58804, Test precision: 0.53714, Test ROC-AUC: 0.49405, Test recall: 0.65102
Predicted: 
uniqs:  tensor([3829,   75])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([ 122, 3782])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([ 273, 3631])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([2594, 1310])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([2517, 1387])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([2745, 1159])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.85454 | Mean Train Acc: 49.34% | Val Loss: 0.69114 | Val accuracy: 51.12%
Epoch: 1 | Mean Tra

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 52.36%, Test F1: 0.61613, Test precision: 0.54672, Test ROC-AUC: 0.50706, Test recall: 0.70596


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [78]:
eval_model('KMeans_Explicit', is_baseline=False, is_naive=False, connection_matrix=matrix_kmeans, relation_type=True)

Predicted: 
uniqs:  tensor([3656,  248])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([   2, 3902])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69240 | Mean Train Acc: 52.27% | Val Loss: 0.69790 | Val accuracy: 44.41%
Epoch: 1 | Mean Train F1: 0.62749 | Mean Train Precision: 0.52812 | Val F1: 0.61036 | Val precision: 0.44350
Epoch: 1 | Mean Train ROC-AUC: 0.49974 | Mean Train Recall: 0

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 53.39%, Test F1: 0.68010, Test precision: 0.54156, Test ROC-AUC: 0.49964, Test recall: 0.91489
Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([  58, 3846])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([  17, 3887])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([ 119, 3785])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([  84, 3820])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([ 3, 58])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69308 | Mean Train Acc: 51.90% | Val Loss: 0.69879 | Val accuracy: 46.56%
Epoch: 1 | Mean Train F1: 0

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.71, Test accuracy: 45.71%, Test F1: 0.09748, Test precision: 0.49339, Test ROC-AUC: 0.49365, Test recall: 0.05412


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [79]:
#eval_model('KMeans_Implicit', is_baseline=False, is_naive=False, connection_matrix=matrix_kmeans, relation_type=False)

### Hierarchical

In [ ]:
matrix_hierarchical = np.load('matrix_hierarchical.npy')

In [ ]:
eval_model('Hierarchical_Naive', is_baseline=False, is_naive=True, connection_matrix=matrix_hierarchical)

Predicted: 
uniqs:  tensor([2283, 1621])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([   1, 3903])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3818,   86])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([1335, 2569])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([1644, 2260])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([2240, 1664])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.97765 | Mean Train Acc: 49.24% | Val Loss: 0.72302 | Val accuracy: 46.79%
Epoch: 1 | Mean Train F1: 0.38669 | Mean Train Precision: 0.38802 | Val F1: 0.41501 | Val precision: 0.42517
Epoch: 1 | Mean Train ROC-AUC: 0.4997

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.70, Test accuracy: 51.38%, Test F1: 0.61225, Test precision: 0.53887, Test ROC-AUC: 0.49626, Test recall: 0.70933
Predicted: 
uniqs:  tensor([3833,   71])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([ 122, 3782])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([1367, 2537])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([2615, 1289])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([1747, 2157])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([1856, 2048])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.84984 | Mean Train Acc: 49.25% | Val Loss: 0.69463 | Val accuracy: 48.99%
Epoch: 1 | Mean Tra

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 52.42%, Test F1: 0.60639, Test precision: 0.54947, Test ROC-AUC: 0.51043, Test recall: 0.67668


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
eval_model('Hierarchical_Explicit', is_baseline=False, is_naive=False, connection_matrix=matrix_hierarchical, relation_type=True)

Predicted: 
uniqs:  tensor([3661,  243])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([  30, 3874])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([52,  9])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69269 | Mean Train Acc: 50.81% | Val Loss: 0.69631 | Val accuracy: 44.32%
Epoch: 1 | Mean Train F1: 0.57130 | Mean Train Precision: 0.52592 | Val F1: 0.61000 | Val precision: 0.44316
Epoch: 1 | Mean Train ROC-AUC: 0.49914 | Mean Train Recal

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.70, Test accuracy: 52.81%, Test F1: 0.66127, Test precision: 0.54120, Test ROC-AUC: 0.49915, Test recall: 0.85074
Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([  58, 3846])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([ 304, 3600])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([ 1, 60])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69337 | Mean Train Acc: 51.96% | Val Loss: 0.69946 | Val accuracy: 44.32%
Epoch: 1 | Mean Train F1: 0.61094 | Mea

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.71, Test accuracy: 48.05%, Test F1: 0.35492, Test precision: 0.54211, Test ROC-AUC: 0.50018, Test recall: 0.26384


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
#eval_model('Hierarchical_Implicit', is_baseline=False, is_naive=False, connection_matrix=matrix_hierarchical, relation_type=False)

### Weighted VRAE

In [51]:
matrix_weighted_vrae = np.load('matrix_weighted_vrae.npy')

In [57]:
eval_model('Weighted_VRAE_Naive', is_baseline=False, is_naive=True, connection_matrix=matrix_weighted_vrae)

Predicted: 
uniqs:  tensor([3625,  279])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([ 133, 3771])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([2263, 1641])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([2949,  955])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([ 427, 3477])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3140,  764])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.90835 | Mean Train Acc: 49.07% | Val Loss: 0.69357 | Val accuracy: 48.87%
Epoch: 1 | Mean Train F1: 0.36107 | Mean Train Precision: 0.41022 | Val F1: 0.43902 | Val precision: 0.42240
Epoch: 1 | Mean Train ROC-AUC: 0.5035

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 54.17%, Test F1: 0.70269, Test precision: 0.54172, Test ROC-AUC: 0.50000, Test recall: 1.00000
Predicted: 
uniqs:  tensor([3564,  340])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3557,  347])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([ 149, 3755])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3577,  327])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([ 285, 3619])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([ 108, 3796])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.83928 | Mean Train Acc: 50.33% | Val Loss: 0.72976 | Val accuracy: 44.41%
Epoch: 1 | Mean Tra

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 54.17%, Test F1: 0.70269, Test precision: 0.54172, Test ROC-AUC: 0.50000, Test recall: 1.00000


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [58]:
eval_model('Weighted_VRAE_Explicit', is_baseline=False, is_naive=False, connection_matrix=matrix_weighted_vrae, relation_type=True)

Predicted: 
uniqs:  tensor([3359,  545])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([  23, 3881])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([  84, 3820])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([   1, 3903])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([   1, 3903])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([   4, 3900])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([1566, 2338])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([ 3, 58])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69884 | Mean Train Acc: 51.81% | Val Loss: 0.69340 | Val accuracy: 49.30%
Epoch: 1 | Mean Train F1: 0.54912 | Mean Train Precision: 0.47328 | Val F1: 0.56673 | Val precision: 0.45830
Epoch: 1 | Mean Train ROC-A

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.70, Test accuracy: 52.98%, Test F1: 0.66245, Test precision: 0.54238, Test ROC-AUC: 0.50099, Test recall: 0.85178
Predicted: 
uniqs:  tensor([   6, 3898])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3752,  152])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([2753, 1151])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([ 127, 3777])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([  34, 3870])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([  54, 3850])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([28, 33])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69464 | Mean Train Acc: 51.70% | Val Loss: 0.70049 | Val accuracy: 44.29%
Epoch: 1 | Mean

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.70, Test accuracy: 53.32%, Test F1: 0.65210, Test precision: 0.54700, Test ROC-AUC: 0.50846, Test recall: 0.80773


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [59]:
#eval_model('Weighted_VRAE_Implicit', is_baseline=False, is_naive=False, connection_matrix=matrix_weighted_vrae, relation_type=False)

### Weighted K-Means

In [61]:
matrix_weighted_kmeans = np.load('matrix_weighted_kmeans.npy')

In [62]:
eval_model('Weighted_KMeans_Naive', is_baseline=False, is_naive=True, connection_matrix=matrix_weighted_kmeans)

Predicted: 
uniqs:  tensor([1618, 2286])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([ 259, 3645])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([ 188, 3716])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([ 312, 3592])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([2415, 1489])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([41, 20])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.75226 | Mean Train Acc: 50.52% | Val Loss: 0.68938 | Val accuracy: 54.09%
Epoch: 1 | Mean Train F1: 0.53252 | Mean Train Precision: 0.47012 | Val F1: 0.14444 | Val precision: 0.40288
Epoch: 1 | Mean Train ROC-AUC: 0.49866 

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 54.17%, Test F1: 0.70269, Test precision: 0.54172, Test ROC-AUC: 0.50000, Test recall: 1.00000
Predicted: 
uniqs:  tensor([3043,  861])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([2347, 1557])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([   5, 3899])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([1422, 2482])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3834,   70])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([2930,  974])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([1676, 2228])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([ 897, 3007])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([ 9, 52])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.70998 | Mean Train Acc: 50.66% | Val Loss: 0.71813 | Val accuracy: 45.51%
Epo

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 54.17%, Test F1: 0.70269, Test precision: 0.54172, Test ROC-AUC: 0.50000, Test recall: 1.00000


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [63]:
eval_model('Weighted_KMeans_Explicit', is_baseline=False, is_naive=False, connection_matrix=matrix_weighted_kmeans, relation_type=True)

Predicted: 
uniqs:  tensor([3489,  415])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([ 185, 3719])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([ 127, 3777])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([ 369, 3535])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([ 118, 3786])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([ 399, 3505])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([ 237, 3667])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([ 295, 3609])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([ 6, 55])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69364 | Mean Train Acc: 51.98% | Val Loss: 0.70587 | Val accuracy: 44.68%
Epoch: 1 | Mean Train F1: 0.61974 | Mean Train Precision: 0.52930 | Val F1: 0.60134 | Val precision: 0.44303
Epoch: 1 | Mean Train

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 53.48%, Test F1: 0.67766, Test precision: 0.54244, Test ROC-AUC: 0.50131, Test recall: 0.90289
Predicted: 
uniqs:  tensor([3894,   10])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3392,  512])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3582,  322])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([   5, 3899])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([ 291, 3613])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([ 504, 3400])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([ 474, 3430])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([ 341, 3563])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([ 1, 60])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.70408 | Mean Train Acc: 50.63% | Val Loss: 0.70230 | Val accuracy: 45.04%
Epo

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 54.03%, Test F1: 0.69856, Test precision: 0.54168, Test ROC-AUC: 0.49993, Test recall: 0.98356


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [64]:
#eval_model('Weighted_KMeans_Implicit', is_baseline=False, is_naive=False, connection_matrix=matrix_weighted_kmeans, relation_type=False)

### Weighted SOM

In [65]:
matrix_weighted_som = np.load('matrix_weighted_som.npy')

In [66]:
eval_model('Weighted_SOM_Naive', is_baseline=False, is_naive=True, connection_matrix=matrix_weighted_som )

Predicted: 
uniqs:  tensor([1725, 2179])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3733,  171])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([ 153, 3751])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([ 660, 3244])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([2605, 1299])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3365,  539])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([1732, 2172])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([2918,  986])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([ 4, 57])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.70817 | Mean Train Acc: 50.60% | Val Loss: 0.70175 | Val accuracy: 49.03%
Epoch: 1 | Mean Train F1: 0.46292 | Mean Train Precision: 0.52826 | Val F1: 0.52985 | Val precision: 0.44894
Epoch: 1 | Mean Train

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 54.17%, Test F1: 0.70269, Test precision: 0.54172, Test ROC-AUC: 0.50000, Test recall: 1.00000
Predicted: 
uniqs:  tensor([3012,  892])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([   7, 3897])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([  12, 3892])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([2914,  990])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([ 339, 3565])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([1028, 2876])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([2199, 1705])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([2727, 1177])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([49, 12])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.71720 | Mean Train Acc: 49.54% | Val Loss: 0.69555 | Val accuracy: 49.30%
Epo

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 54.17%, Test F1: 0.70269, Test precision: 0.54172, Test ROC-AUC: 0.50000, Test recall: 1.00000


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [67]:
eval_model('Weighted_SOM_Explicit', is_baseline=False, is_naive=False, connection_matrix=matrix_weighted_som, relation_type=True)

Predicted: 
uniqs:  tensor([3512,  392])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([   5, 3899])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([ 161, 3743])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([ 260, 3644])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([ 170, 3734])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([ 239, 3665])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([ 118, 3786])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([  15, 3889])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69870 | Mean Train Acc: 52.19% | Val Loss: 0.70408 | Val accuracy: 44.82%
Epoch: 1 | Mean Train F1: 0.62750 | Mean Train Precision: 0.53082 | Val F1: 0.58993 | Val precision: 0.44103
Epoch: 1 | Mean Train ROC

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 54.39%, Test F1: 0.70055, Test precision: 0.54360, Test ROC-AUC: 0.50373, Test recall: 0.98519
Predicted: 
uniqs:  tensor([3899,    5])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3457,  447])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3663,  241])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([  11, 3893])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([ 444, 3460])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([ 371, 3533])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([ 196, 3708])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([  76, 3828])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69785 | Mean Train Acc: 50.85% | Val Loss: 0.70678 | Val accuracy: 44.32%
Epoch: 

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 53.55%, Test F1: 0.67491, Test precision: 0.54349, Test ROC-AUC: 0.50318, Test recall: 0.89031


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [68]:
#eval_model('Weighted_SOM_Implicit', is_baseline=False, is_naive=False, connection_matrix=matrix_weighted_som, relation_type=False)

### Weighted Hierarchical

In [26]:
matrix_weighted_hierarchical = np.load('matrix_weighted_hierarchical.npy')

In [27]:
eval_model('Weighted_Hierarchical_Naive', is_baseline=False, is_naive=True, connection_matrix=matrix_weighted_hierarchical)

Predicted: 
uniqs:  tensor([2507, 1397])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([ 443, 3461])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([1740, 2164])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([1263, 2641])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([ 909, 2995])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([50, 11])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.96936 | Mean Train Acc: 49.37% | Val Loss: 0.71068 | Val accuracy: 47.93%
Epoch: 1 | Mean Train F1: 0.49022 | Mean Train Precision: 0.45663 | Val F1: 0.51506 | Val precision: 0.43005
Epoch: 1 | Mean Train ROC-AUC: 0.49251 

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 52.39%, Test F1: 0.63442, Test precision: 0.54319, Test ROC-AUC: 0.50227, Test recall: 0.76281
Predicted: 
uniqs:  tensor([3692,  212])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3726,  178])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([ 547, 3357])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([ 501, 3403])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([1099, 2805])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([21, 40])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.93077 | Mean Train Acc: 48.93% | Val Loss: 0.70703 | Val accuracy: 45.05%
Epoch: 1 | Mean Train

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 54.17%, Test F1: 0.70269, Test precision: 0.54172, Test ROC-AUC: 0.50000, Test recall: 1.00000


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
eval_model('Weighted_Hierarchical_Explicit', is_baseline=False, is_naive=False, connection_matrix=matrix_weighted_hierarchical, relation_type=True)

Predicted: 
uniqs:  tensor([3326,  578])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([ 207, 3697])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69644 | Mean Train Acc: 51.72% | Val Loss: 0.69527 | Val accuracy: 44.42%
Epoch: 1 | Mean Train F1: 0.56217 | Mean Train Precision: 0.46914 | Val F1: 0.61026 | Val precision: 0.44358
Epoch: 1 | Mean Train ROC-AUC: 0.49973 | Mean Train Recall: 0

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.71, Test accuracy: 52.83%, Test F1: 0.60994, Test precision: 0.55269, Test ROC-AUC: 0.51469, Test recall: 0.68095
Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([  25, 3879])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([ 201, 3703])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69583 | Mean Train Acc: 51.69% | Val Loss: 0.69512 | Val accuracy: 44.32%
Epoch: 1 | Mean Train F1: 0.53753 | Mean Tr

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.70, Test accuracy: 53.57%, Test F1: 0.66014, Test precision: 0.54719, Test ROC-AUC: 0.50902, Test recall: 0.83263


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
#eval_model('Weighted_Hierarchical_Implicit', is_baseline=False, is_naive=False, connection_matrix=matrix_weighted_hierarchical, relation_type=False)

## Tatyana: Exogenous linkages

In [ ]:
reports_matrix_3_parameters = np.load('financial_reports_2d_relational_matrix.npy')

In [ ]:
reports_matrix_2_parameters = np.load('2_variant_financial_reports_2d_relational_matrix.npy')

In [ ]:
reports_matrix_0_3 = np.load('from_0_to_3_financial_reports_2d_relational_matrix.npy')

In [ ]:
eval_model('Reports_3_par_Naive', is_baseline=False, is_naive=True, connection_matrix=reports_matrix_3_parameters)

Predicted: 
uniqs:  tensor([1567, 2337])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3782,  122])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([2191, 1713])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3588,  316])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3409,  495])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([60,  1])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.85581 | Mean Train Acc: 49.33% | Val Loss: 0.73839 | Val accuracy: 48.10%
Epoch: 1 | Mean Train F1: 0.32023 | Mean Train Precision: 0.49505 | Val F1: 0.53213 | Val precision: 0.42929
Epoch: 1 | Mean Train ROC-AUC: 0.50132 

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 52.49%, Test F1: 0.61412, Test precision: 0.54827, Test ROC-AUC: 0.50905, Test recall: 0.69803
Predicted: 
uniqs:  tensor([3892,   12])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([  61, 3843])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([  21, 3883])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([  39, 3865])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3851,   53])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.81657 | Mean Train Acc: 49.58% | Val Loss: 0.68834 | Val accuracy: 55.83%
Epoch: 1 | Mean Train F1:

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.70, Test accuracy: 50.01%, Test F1: 0.50763, Test precision: 0.54411, Test ROC-AUC: 0.50252, Test recall: 0.47611


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
eval_model('Reports_3_par_Explicit', is_baseline=False, is_naive=False, connection_matrix=reports_matrix_3_parameters, relation_type=True)

Predicted: 
uniqs:  tensor([3755,  149])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69227 | Mean Train Acc: 52.27% | Val Loss: 0.69931 | Val accuracy: 44.32%
Epoch: 1 | Mean Train F1: 0.62307 | Mean Train Precision: 0.52894 | Val F1: 0.61000 | Val precision: 0.44316
Epoch: 1 | Mean Train ROC-AUC: 0.49990 | Mean Train Recall: 0.89304

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.72, Test accuracy: 47.67%, Test F1: 0.32429, Test precision: 0.53966, Test ROC-AUC: 0.49892, Test recall: 0.23179
Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([ 121, 3783])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([ 414, 3490])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69297 | Mean Train Acc: 52.07% | Val Loss: 0.69969 | Val accuracy: 44.32%
Epoch: 1 | Mean Train F1: 0.61081 | Mean Tr

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.71, Test accuracy: 47.59%, Test F1: 0.33010, Test precision: 0.53681, Test ROC-AUC: 0.49746, Test recall: 0.23833


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
#eval_model('Reports_3_par_Implicit', is_baseline=False, is_naive=False, connection_matrix=reports_matrix_3_parameters, relation_type=False)

In [ ]:
eval_model('Reports_2_par_Naive', is_baseline=False, is_naive=True, connection_matrix=reports_matrix_2_parameters)

Predicted: 
uniqs:  tensor([1567, 2337])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3782,  122])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([2191, 1713])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3588,  316])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3409,  495])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([60,  1])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.85581 | Mean Train Acc: 49.33% | Val Loss: 0.73839 | Val accuracy: 48.10%
Epoch: 1 | Mean Train F1: 0.32023 | Mean Train Precision: 0.49505 | Val F1: 0.53213 | Val precision: 0.42929
Epoch: 1 | Mean Train ROC-AUC: 0.50132 

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 52.49%, Test F1: 0.61412, Test precision: 0.54827, Test ROC-AUC: 0.50905, Test recall: 0.69803
Predicted: 
uniqs:  tensor([3892,   12])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([  61, 3843])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([  21, 3883])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([  39, 3865])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3851,   53])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.81657 | Mean Train Acc: 49.58% | Val Loss: 0.68834 | Val accuracy: 55.83%
Epoch: 1 | Mean Train F1:

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.70, Test accuracy: 50.01%, Test F1: 0.50763, Test precision: 0.54411, Test ROC-AUC: 0.50252, Test recall: 0.47611


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
eval_model('Reports_2_par_Explicit', is_baseline=False, is_naive=False, connection_matrix=reports_matrix_2_parameters, relation_type=True)

Predicted: 
uniqs:  tensor([3755,  149])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69227 | Mean Train Acc: 52.27% | Val Loss: 0.69931 | Val accuracy: 44.32%
Epoch: 1 | Mean Train F1: 0.62307 | Mean Train Precision: 0.52894 | Val F1: 0.61000 | Val precision: 0.44316
Epoch: 1 | Mean Train ROC-AUC: 0.49990 | Mean Train Recall: 0.89304

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.72, Test accuracy: 47.67%, Test F1: 0.32429, Test precision: 0.53966, Test ROC-AUC: 0.49892, Test recall: 0.23179
Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([ 121, 3783])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([ 414, 3490])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69297 | Mean Train Acc: 52.07% | Val Loss: 0.69969 | Val accuracy: 44.32%
Epoch: 1 | Mean Train F1: 0.61081 | Mean Tr

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.71, Test accuracy: 47.59%, Test F1: 0.33010, Test precision: 0.53681, Test ROC-AUC: 0.49746, Test recall: 0.23833


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
#eval_model('Reports_2_par_Implicit', is_baseline=False, is_naive=False, connection_matrix=reports_matrix_2_parameters, relation_type=False)

In [ ]:
eval_model('Reports_0_to_3_Naive', is_baseline=False, is_naive=True, connection_matrix=reports_matrix_0_3)

Predicted: 
uniqs:  tensor([2643, 1261])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([ 136, 3768])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([ 565, 3339])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3843,   61])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3141,  763])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([2387, 1517])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.99393 | Mean Train Acc: 48.64% | Val Loss: 0.72984 | Val accuracy: 49.11%
Epoch: 1 | Mean Train F1: 0.35008 | Mean Train Precision: 0.43323 | Val F1: 0.50157 | Val precision: 0.43193
Epoch: 1 | Mean Train ROC-AUC: 0.4943

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 52.38%, Test F1: 0.66976, Test precision: 0.53631, Test ROC-AUC: 0.49064, Test recall: 0.89256
Predicted: 
uniqs:  tensor([3779,  125])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([  61, 3843])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([ 432, 3472])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([ 738, 3166])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([2078, 1826])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([50, 11])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.92756 | Mean Train Acc: 47.54% | Val Loss: 0.69863 | Val accuracy: 52.21%
Epoch: 1 | Mean Train

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 54.17%, Test F1: 0.70269, Test precision: 0.54172, Test ROC-AUC: 0.50000, Test recall: 1.00000


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
eval_model('Reports_0_to_3_Explicit', is_baseline=False, is_naive=False, connection_matrix=reports_matrix_0_3, relation_type=True)

Predicted: 
uniqs:  tensor([3525,  379])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3892,   12])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69403 | Mean Train Acc: 51.63% | Val Loss: 0.69790 | Val accuracy: 44.32%
Epoch: 1 | Mean Train F1: 0.55595 | Mean Train Precision: 0.53078 | Val F1: 0.61000 | Val precision: 0.44316
Epoch: 1 | Mean Train ROC-AUC: 0.49891 | Mean Train Recall: 0

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.71, Test accuracy: 53.86%, Test F1: 0.67577, Test precision: 0.54578, Test ROC-AUC: 0.50716, Test recall: 0.88764
Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([  35, 3869])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3783,  121])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([ 3, 58])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69350 | Mean Train Acc: 51.22% | Val Loss: 0.69618 | Val accuracy: 44.32%
Epoch: 1 | Mean Train F1: 0.54165 | Mea

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.72, Test accuracy: 52.02%, Test F1: 0.60502, Test precision: 0.54620, Test ROC-AUC: 0.50605, Test recall: 0.67845


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
#eval_model('Reports_0_to_3_Implicit', is_baseline=False, is_naive=False, connection_matrix=reports_matrix_0_3, relation_type=False)

## Ksenia: Learnable linkages

### Weighted Wiki

In [30]:
matrix_weighted_wiki = np.load('2d_matrix_61x61_wiki_relation.npy')

In [31]:
eval_model('Weighted_Wiki_Naive', is_baseline=False, is_naive=True, connection_matrix=matrix_weighted_wiki)

Predicted: 
uniqs:  tensor([2326, 1578])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([2982,  922])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([1644, 2260])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([ 183, 3721])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([ 122, 3782])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.98811 | Mean Train Acc: 49.32% | Val Loss: 0.69244 | Val accuracy: 53.97%
Epoch: 1 | Mean Train F1: 0.44680 | Mean Train Precision: 0.40155 | Val F1: 0.48963 | Val precision: 0.48824
Epoch: 1 | Mean Train ROC-AUC: 0.49793 | Me

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.70, Test accuracy: 53.21%, Test F1: 0.62968, Test precision: 0.55169, Test ROC-AUC: 0.51415, Test recall: 0.73424
Predicted: 
uniqs:  tensor([3782,  122])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([ 122, 3782])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3895,    9])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([1663, 2241])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([ 416, 3488])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([ 686, 3218])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.85836 | Mean Train Acc: 48.97% | Val Loss: 0.69479 | Val accuracy: 49.63%
Epoch: 1 | Mean Tra

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 52.55%, Test F1: 0.63515, Test precision: 0.54425, Test ROC-AUC: 0.50384, Test recall: 0.76259


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [32]:
eval_model('Weighted_Wiki_Explicit', is_baseline=False, is_naive=False, connection_matrix=matrix_weighted_wiki, relation_type=True)

Predicted: 
uniqs:  tensor([3612,  292])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3419,  485])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([  99, 3805])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([19, 42])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69297 | Mean Train Acc: 51.29% | Val Loss: 0.69568 | Val accuracy: 44.16%
Epoch: 1 | Mean Train F1: 0.56404 | Mean Train Precision: 0.53139 | Val F1: 0.60278 | Val precision: 0.44080
Epoch: 1 | Mean Train ROC-AUC: 0.50023 | Mean Train

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.71, Test accuracy: 48.34%, Test F1: 0.34921, Test precision: 0.54980, Test ROC-AUC: 0.50401, Test recall: 0.25587
Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([  53, 3851])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([18, 43])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.69331 | Mean Train Acc: 51.89% | Val Loss: 0.70001 | Val accuracy: 44.32%
Epoch: 1 | Mean Train F1: 0.60528 | Mean Trai

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.71, Test accuracy: 47.99%, Test F1: 0.34093, Test precision: 0.54378, Test ROC-AUC: 0.50094, Test recall: 0.24832


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

### Reasonable Weighted Wiki

In [ ]:
matrix_weighted_wiki = np.load('43_2d_matrix_61x61_wiki_relation.npy')

In [ ]:
eval_model('Reasonable_Weighted_Wiki_Naive', is_baseline=False, is_naive=True, connection_matrix=matrix_weighted_wiki)

Predicted: 
uniqs:  tensor([2299, 1605])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([  88, 3816])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([ 856, 3048])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([1084, 2820])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([1158, 2746])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([2044, 1860])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.90066 | Mean Train Acc: 49.81% | Val Loss: 0.69845 | Val accuracy: 50.57%
Epoch: 1 | Mean Train F1: 0.46328 | Mean Train Precision: 0.40809 | Val F1: 0.50962 | Val precision: 0.43508
Epoch: 1 | Mean Train ROC-AUC: 0.5004

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 52.75%, Test F1: 0.57250, Test precision: 0.56191, Test ROC-AUC: 0.52273, Test recall: 0.58416
Predicted: 
uniqs:  tensor([3144,  760])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3600,  304])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([  98, 3806])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([  60, 3844])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([  53, 3851])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([ 178, 3726])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([61])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.94324 | Mean Train Acc: 49.75% | Val Loss: 0.70103 | Val accuracy: 48.75%
Epoch: 1 | Mean Tra

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 52.74%, Test F1: 0.68802, Test precision: 0.53571, Test ROC-AUC: 0.48822, Test recall: 0.96212


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
eval_model('Reasonable_Weighted_Wiki_Explicit', is_baseline=False, is_naive=False, connection_matrix=matrix_weighted_wiki, relation_type=True)

Predicted: 
uniqs:  tensor([3153,  751])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3300,  604])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([   9, 3895])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([ 338, 3566])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([ 279, 3625])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([  31, 3873])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([  36, 3868])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([ 1, 60])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.70818 | Mean Train Acc: 51.46% | Val Loss: 0.69578 | Val accuracy: 45.68%
Epoch: 1 | Mean Train F1: 0.58806 | Mean Train Precision: 0.52463 | Val F1: 0.59305 | Val precision: 0.44443
Epoch: 1 | Mean Train ROC-A

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.70, Test accuracy: 53.60%, Test F1: 0.65861, Test precision: 0.54774, Test ROC-AUC: 0.50985, Test recall: 0.82629
Predicted: 
uniqs:  tensor([3893,   11])
Ground truth: 
uniqs:  tensor([1816, 2088])

Predicted: 
uniqs:  tensor([ 705, 3199])
Ground truth: 
uniqs:  tensor([1836, 2068])

Predicted: 
uniqs:  tensor([3904])
Ground truth: 
uniqs:  tensor([1850, 2054])

Predicted: 
uniqs:  tensor([3654,  250])
Ground truth: 
uniqs:  tensor([1839, 2065])

Predicted: 
uniqs:  tensor([ 118, 3786])
Ground truth: 
uniqs:  tensor([1846, 2058])

Predicted: 
uniqs:  tensor([  17, 3887])
Ground truth: 
uniqs:  tensor([1809, 2095])

Predicted: 
uniqs:  tensor([   5, 3899])
Ground truth: 
uniqs:  tensor([1983, 1921])

Predicted: 
uniqs:  tensor([  76, 3828])
Ground truth: 
uniqs:  tensor([1864, 2040])

Predicted: 
uniqs:  tensor([ 2, 59])
Ground truth: 
uniqs:  tensor([26, 35])

Epoch: 1 | Mean Train Loss: 0.71547 | Mean Train Acc: 50.67% | Val Loss: 0.69489 | Val accuracy: 45.81%
Epoch: 1 

<IPython.core.display.Javascript object>

...

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Test Loss: 0.69, Test accuracy: 53.59%, Test F1: 0.67139, Test precision: 0.54487, Test ROC-AUC: 0.50540, Test recall: 0.87531


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [ ]:
#eval_model('Reasonable_Weighted_Wiki_Implicit', is_baseline=False, is_naive=False, connection_matrix=matrix_weighted_wiki, relation_type=False)